In [1]:
!pip install dlisio==0.3.5
!pip install lasio

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


In [2]:
from dlisio import dlis
import lasio

with dlis.load(r'C:\Users\joseaugustodias\Desktop\1ogx93ma_raw1_006.dlis') as files:
    for f in files:
        for frame in f.frames:
            curves = frame.curves()
            # Do something with the curves

In [3]:
for i in curves:
    print(i)

(1, 480314., 15.117695, 2965.6394, 4149.932, 41.666664, 9.756278, 3872.5007)
(2, 480312., 15.098298, 2650.9045, 3757.4604, 33.333332, 9.6831875, 4056.808)
(3, 480310., 15.179429, 2042.4685, 3874.3325, 33.333332, 9.793362, 4391.7363)
(4, 480308., 15.213082, 4005.1272, 3251.211, 33.333332, 9.753054, 2909.8132)
(5, 480306., 15.296822, 2849.3477, 3377.308, 33.333332, 9.812172, 4719.495)
(6, 480304., 15.271521, 2857.5347, 2456.8267, 49.999996, 9.77276, 3183.6003)
(7, 480302., 15.310852, 4329.9736, 3789.4167, 66.666664, 9.715433, 3959.637)
(8, 480300., 15.320201, 4526.399, 4148.047, 41.666664, 9.702536, 4787.305)
(9, 480298., 15.382552, 4449.779, 3025.3772, 33.333332, 9.753054, 4379.756)
(10, 480296., 15.34972, 4236.8647, 3697.933, 33.333332, 9.755741, 4132.5654)
(11, 480294., 15.450347, 4749.978, 3422.8127, 33.333332, 9.734243, 4558.6094)
(12, 480292., 15.412509, 5000., 3955.449, 33.333332, 9.787987, 3252.2412)
(13, 480290., 15.407229, 4878.72, 3301.8425, 33.333332, 9.796049, 4347.75)
(14, 

In [4]:
import numpy as np
print(np.shape(curves))

(28543,)


In [5]:
len(curves[0])

8

In [6]:
curves = np.array(curves).T

In [7]:
curves

array([(    1, 480314., 15.117695, 2965.6394, 4149.932 ,  41.666664, 9.756278 , 3872.5007),
       (    2, 480312., 15.098298, 2650.9045, 3757.4604,  33.333332, 9.6831875, 4056.808 ),
       (    3, 480310., 15.179429, 2042.4685, 3874.3325,  33.333332, 9.793362 , 4391.7363),
       ...,
       (28541, 423234., 13.759291, 4764.355 , 3222.6348,  83.333336, 9.744067 , 5000.    ),
       (28542, 423232., 13.92569 , 4914.7876, 3336.5815, 116.66668 , 9.739308 , 4183.502 ),
       (28543, 423230., 13.962658, 5000.    , 4066.7563, 133.33334 , 9.777114 , 5000.    )],
      dtype=[('FRAMENO', '<i4'), (('T.CHANNEL-I.TDEP-O.124-C.6', 'TDEP'), '<f4'), (('T.CHANNEL-I.RXGR-O.124-C.0', 'RXGR'), '<f4'), (('T.CHANNEL-I.RXRU-O.124-C.0', 'RXRU'), '<f4'), (('T.CHANNEL-I.RVSRU-O.124-C.0', 'RVSRU'), '<f4'), (('T.CHANNEL-I.FTIM-O.124-C.0', 'FTIM'), '<f4'), (('T.CHANNEL-I.FCAZ-O.124-C.0', 'FCAZ'), '<f4'), (('T.CHANNEL-I.RVDRU-O.124-C.0', 'RVDRU'), '<f4')])

In [8]:
mtx = []
for i in curves:
    a = list(i)
    mtx.append(a)
    
mtx = np.array(mtx)
print(mtx[:,3])

[2965.6394043  2650.90454102 2042.46850586 ... 4764.35498047 4914.78759766
 5000.        ]


In [9]:
import os
import dlisio
import pandas as pd

def process_curve_info(channel_data):
    def df_column_uniquify(df):
        df_columns = df.columns
        new_columns = []
        print('AQUI')
        for item in df_columns:
            counter = 0
            newitem = item
            while newitem in new_columns:
                counter += 1
                newitem = "{}_{}".format(item, counter)
            new_columns.append(newitem)
        df.columns = new_columns
        return df

    for name_index, c in enumerate(channel_data["curves_L"]):
        name = channel_data["curves_name"][name_index]
        print("Processing " + name)
        units = channel_data["unit"][name_index]
        long = channel_data["longs"][name_index]
        c = np.vstack(c)
        try:
            num_col = c.shape[1]
            col_name = [name] * num_col
            df = pd.DataFrame(data=c, columns=col_name)
            channel_data["curve_df"] = pd.concat([channel_data["curve_df"], df], axis=1)
            object_warning = str(
                name) + ' had to be expanded in the final .las file, as it has multiple samples per index'
        except:
            num_col = 1
            df = pd.DataFrame(data=c, columns=[name])
            channel_data["curve_df"] = pd.concat([channel_data["curve_df"], df], axis=1)
            continue
        u = [units] * num_col
        l = [long] * num_col
        channel_data["las_units"].append(u)
        channel_data["las_longs"].append(l)
        print("Completed " + name)

    las_units = [item for sublist in channel_data["las_units"] for item in sublist]
    las_longs = [item for sublist in channel_data["las_longs"] for item in sublist]

    # Check that the lists are ready for the curve metadata
    print("If these are different lengths, something is wrong:")
    print(len(las_units))
    print(len(las_longs))
    
    return channel_data

    #curve_df = df_column_uniquify(channel_data["curve_df"])
    #return las_units, las_longs, curve_df, object_warning

def create_las(curve_df, curves_name, origin, las_units, las_longs, null, filepath):
    las = lasio.LASFile()
    # write the pandas data to the las file
    las.set_data(curve_df)
    # write the curve metadata from our three lists.
    counter = 0
    for x in curves_name:
        las.curves[x].unit = las_units[counter]
        las.curves[x].descr = las_longs[counter]
        counter = counter + 1
    las.well.COMP = origin.company
    las.well.WELL = origin.well_name
    las.well.FLD = origin.field_name
    las.well.SRVC = origin.producer_name
    las.well.DATE = origin.creation_time
    las.well.UWI = origin.well_id
    las.well.API = origin.well_id
    las.well.NULL = null
    las.params['PROD'] = lasio.HeaderItem('PROD', value=origin.product)
    las.params['PROG'] = lasio.HeaderItem('PROG', value=origin.programs)
    las.params['RUN'] = lasio.HeaderItem('RUN', value=origin.run_nr)
    las.params['DESCENT'] = lasio.HeaderItem('DESCENT', value=origin.descent_nr)
    las.params['VERSION'] = lasio.HeaderItem('VERSION', value=origin.version)
    las.params['LINEAGE'] = lasio.HeaderItem('LINEAGE', value="Python-converted from DLIS")
    las.params['ORFILE'] = lasio.HeaderItem('ORFILE', value=filepath)
    return las
    

def convert_dlis_to_las(filepath, output_folder_location, null=-999.25):
    filename = os.path.basename(filepath)
    filename = os.path.splitext(filename)[0]
    embedded_files = []
    origins = []

    with dlisio.dlis.load(filepath) as file:
        print(file.describe())
        for d in file:
            embedded_files.append(d)
            frame_count = 0
            for origin in d.origins:
                origins.append(origin)
            for fram in d.frames:
                frame_count = frame_count + 1

                channel_data = {
                    "curves_name": [],
                    "longs": [],
                    "unit": [],
                    "curves_L": [],
                    "curve_df": pd.DataFrame(),
                    "las_units": [],
                    "las_longs": [],
                }

                # -----------------------------------------------------------------------
                # Process channel/curve information
                # -----------------------------------------------------------------------
                for channel in fram.channels:
                    channel_data["curves_name"].append(channel.name)
                    channel_data["longs"].append(channel.long_name)
                    channel_data["unit"].append(channel.units)
                    curves = channel.curves()
                    channel_data["curves_L"].append(curves)
                    
                # Não passa daqui
                #las_units, las_longs, curve_df, object_warning = process_curve_info(
                #    channel_data
                #)
                
                A = process_curve_info(channel_data)
                
                print(A['curves_name'])                
                #print(len(A['curves_L']))
                print(A['unit'])
                
            
                #print(A['curves_L'][0])
                #print(A)
                
                DATA = {}
                for i in range(len(A['curves_name'])):
                    DATA[A['curves_name'][i]] = {}
                    DATA[A['curves_name'][i]]['curve'] = A['curves_L'][i]
                    DATA[A['curves_name'][i]]['unit'] = A['unit'][i]

                #DF = pd.DataFrame(DATA)
                    
                return DATA
                
                #curves_name = list(curve_df.columns.values)
                #print(len(curves_name))
                

                # we will take the first curve in the frame as the index.
                #curve_df = curve_df.set_index(curves_name[0])

                # -----------------------------------------------------------------------
                # Create las file
                # -----------------------------------------------------------------------
                #las = create_las(
                #    curve_df, curves_name, origin, las_units, las_longs, null, filepath
                #)

                # -----------------------------------------------------------------------
                # Write las file
                # -----------------------------------------------------------------------
                #write_las_file(las, filename, frame_count, output_folder_location)

            #print("number of frames: " + str(frame_count) + ": this is the number of .las files created")
            #print("embedded_files: " + str(len(embedded_files)))
            #print("This file has " + str(len(origins)) + " metadata headers.  This code has used the first.")
            #print(object_warning)

In [11]:
DATA = convert_dlis_to_las(
    r'C:\Users\joseaugustodias\Desktop\1ogx93ma_raw1_006.dlis',
    r"C:\Users\zoraida\Desktop\ ", null=-999.25)

-------------
Physical File
-------------
Number of Logical Files : 1

Description : LogicalFile(MaxWell_6Dlis)
Frames      : 7
Channels    : 411


Processing TDEP
Completed TDEP
Processing DT4P
Completed DT4P
Processing RAZ_EDTC
Completed RAZ_EDTC
Processing DRTA
Completed DRTA
Processing S1R1
Completed S1R1
Processing PWF2
Completed PWF2
Processing DTRS
Completed DTRS
Processing DLS
Completed DLS
Processing PSCS
Completed PSCS
Processing SP
Completed SP
Processing SVEL
Completed SVEL
Processing DTSM
Completed DTSM
Processing RSP
Completed RSP
Processing NPHI_DOL
Completed NPHI_DOL
Processing NPR2
Completed NPR2
Processing DCI2
Completed DCI2
Processing TDSP
Completed TDSP
Processing NPOR_SAN
Completed NPOR_SAN
Processing DT4S
Completed DT4S
Processing DNPH
Completed DNPH
Processing TTTS
Completed TTTS
Processing TTTP
Completed TTTP
Processing INCL
Completed INCL
Processing CHR2
Completed CHR2
Processing DTRP
Completed DTRP
Processing GDEV_EDTC
Completed GDEV_EDTC
Processing TNRA
Comp

In [12]:
print(DATA.keys()) #  # 'BTI1', 'CTT1', 'CAL1','TDEP','SDEP','DEP1','U-SEIS_TVDSRD1',

dict_keys(['TDEP', 'DT4P', 'RAZ_EDTC', 'DRTA', 'S1R1', 'PWF2', 'DTRS', 'DLS', 'PSCS', 'SP', 'SVEL', 'DTSM', 'RSP', 'NPHI_DOL', 'NPR2', 'DCI2', 'TDSP', 'NPOR_SAN', 'DT4S', 'DNPH', 'TTTS', 'TTTP', 'INCL', 'CHR2', 'DTRP', 'GDEV_EDTC', 'TNRA', 'GHD', 'DF', 'ED', 'CHTP', 'CHTS', 'TTR1', 'TNPH', 'SPT4', 'CS', 'DTCO', 'GR_EDTC', 'NPOR_LIM', 'SSVE', 'C1R1', 'WF1', 'QCPOR', 'QCBSL', 'T1T4', 'ROAZ', 'ECGR_EDTC', 'T1R4', 'CDF', 'C1R4', 'FF', 'TTR2', 'SPR2', 'TNPH_SAN', 'PWF4', 'RTNR', 'BSD1', 'RWA', 'CFGR', 'WF4', 'SPHI', 'HET', 'RCFT', 'RHET', 'CVEL', 'DCI1', 'ECGR', 'STIT', 'NPR1', 'TTRS', 'SPR4', 'ND', 'BHRM', 'TNPH_DOL', 'BS', 'NPOR_DOL', 'PR', 'CHRP', 'NCYT', 'T1R1', 'RXO', 'NPR4', 'WF2', 'DT2', 'RGR', 'AZIM', 'DEPTH', 'SSLT', 'NPT4', 'BHPR', 'TENS', 'CHR1', 'IDWD', 'TNPH_LIM', 'LSD1', 'TVDSS', 'HV', 'RT', 'TVD', 'TALP', 'C1R2', 'GR', 'C1T4', 'GTEM', 'VPVS', 'SPR1', 'DT2R', 'NPHI_LIM', 'CNTC', 'DI', 'NPHI', 'QCMCFL', 'T1R2', 'TTRP', 'HTEM', 'GDEV', 'DTTS', 'FCD', 'DT1', 'NPOR', 'ATCA', 'PWN4

In [13]:
DATA

{'TDEP': {'curve': array([480300., 480240., 480180., 480120., 480060., 480000., 479940.,
         479880., 479820., 479760., 479700., 479640., 479580., 479520.,
         479460., 479400., 479340., 479280., 479220., 479160., 479100.,
         479040., 478980., 478920., 478860., 478800., 478740., 478680.,
         478620., 478560., 478500., 478440., 478380., 478320., 478260.,
         478200., 478140., 478080., 478020., 477960., 477900., 477840.,
         477780., 477720., 477660., 477600., 477540., 477480., 477420.,
         477360., 477300., 477240., 477180., 477120., 477060., 477000.,
         476940., 476880., 476820., 476760., 476700., 476640., 476580.,
         476520., 476460., 476400., 476340., 476280., 476220., 476160.,
         476100., 476040., 475980., 475920., 475860., 475800., 475740.,
         475680., 475620., 475560., 475500., 475440., 475380., 475320.,
         475260., 475200., 475140., 475080., 475020., 474960., 474900.,
         474840., 474780., 474720., 474660., 47

In [14]:
DATA['RT']

{'curve': array([   5.700751 ,    5.3153715,    5.315812 ,    5.683103 ,
           6.5912213,    7.7356095,    7.5746183,    7.2367506,
           7.3805923,    7.6656585,    7.9933624,    7.9017925,
           7.807803 ,    7.603026 ,    6.6453996,    5.836971 ,
           5.3481617,    5.0246377,    5.0710335,    5.465344 ,
           5.8998256,    5.9468694,    5.8313794,    5.6879344,
           5.622261 ,    5.716843 ,    6.776997 ,    8.079023 ,
           8.172358 ,    8.409516 ,    9.126518 ,    9.796612 ,
           9.236988 ,    8.595563 ,    8.205355 ,    7.5451202,
           7.3155327,    6.1535664,    6.3513813,    6.5755954,
           6.8699546,    7.21311  ,    7.8287544,    7.863304 ,
           7.7575135,    8.222396 ,    9.258765 ,   10.168983 ,
          11.097784 ,   11.494675 ,   10.622255 ,    9.344706 ,
           8.426082 ,    7.4897428,    6.7348833,    5.827676 ,
           5.1167164,    5.2048497,    5.428757 ,    4.928304 ,
           4.6371827,    4.5237

In [39]:
tosave = ['DEPTH','BS','DCAL','GR','NPHI','DT4P','DT4S','RT','RHGX_HILT']

all_data = []
for m in tosave:  
    column = [m] + [DATA[m]['unit']] + list(DATA[m]['curve'])
    all_data.append(column)
    

DF = pd.DataFrame(all_data).T
new_header = DF.iloc[0]
DF = DF[1:]
DF.columns = new_header
DF.to_csv("C:\\Users\\joseaugustodias\\Desktop\\dlis_to_csv.las", index=False)
#Salvará em LAS sem cabeçalho

In [40]:
tosave = ['DEPTH','BS','DCAL','GR','NPHI','DT4P','DT4S','RT','RHGX_HILT']

all_data = []
for m in tosave:  
    column = [m] + [DATA[m]['unit']] + list(DATA[m]['curve'])
    all_data.append(column)
    

DF = pd.DataFrame(all_data).T
new_header = DF.iloc[0]
DF = DF[1:]
DF.columns = new_header
DF.to_csv("C:\\Users\\joseaugustodias\\Desktop\\dlis_to_csv.csv")
#Salvará em CSV